<a href="https://colab.research.google.com/github/anarakinson/Queue_count/blob/main/Queue_count.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
import cv2
from google.colab.patches import cv2_imshow

import json, time
import numpy as np
from PIL import Image

import torch

from moviepy.editor import *
from IPython.display import clear_output

Загрузка модели с Torch hub

In [ ]:
# Model
model = torch.hub.load('ultralytics/yolov5', 'yolov5x')
# Inference
model.classes = [0]  # (опционально) фильтрация по классам, например = [0, 15, 16] оставляет людей, кошек и собак

Using cache found in /root/.cache/torch/hub/ultralytics_yolov5_master
YOLOv5 🚀 2021-7-8 torch 1.9.0+cu102 CUDA:0 (Tesla T4, 15109.75MB)

Fusing layers... 
Model Summary: 476 layers, 87730285 parameters, 0 gradients
Adding AutoShape... 


Обработка видео

In [ ]:
start_time = time.time()
# Создаем объект захвата видео, в этом случае мы читаем видео из файла
vid_capture = cv2.VideoCapture('/content/stock8.mp4')# загружаем видео
if (vid_capture.isOpened() == False):
  print("Ошибка открытия видеофайла")
# Чтение fps и количества кадров
else:
  # Получаем ширину и высоту кадра
  frame_h   = int(vid_capture.get(cv2.CAP_PROP_FRAME_HEIGHT))
  frame_w   = int(vid_capture.get(cv2.CAP_PROP_FRAME_WIDTH))
  # Получить информацию о частоте кадров
  fps       = int(vid_capture.get(cv2.CAP_PROP_FPS))
  print('Фреймов в секунду: ', fps,'FPS')
  # Получить количество кадров
  frame_count = int(vid_capture.get(cv2.CAP_PROP_FRAME_COUNT))
  print('Количество кадров: ', frame_count)
  print('\n-----------------------------\nДля завершения нажмите "q" или Esc...')

images = []

file_count = 0
while True:
    # Метод vid_capture.read() возвращают кортеж, 
    # первым элементом является логическое значение а вторым кадр
    ret, frame = vid_capture.read()
    if not ret:
        break
    
    results = model(frame, size=640)# предикт 
    results.render()# Возвращает отрисованные боксы
    
    n = len(results.pandas().xyxy[0]['class'].tolist())# считаем сколько человек в кадре
    cv2.rectangle(frame, (frame_w, frame_w//2), (0, frame_h), (255, 0, 0), -1) # Рисуем прямоугольник
    cv2.putText(frame, f'сейчас {n} человек в очереди', (20, frame_h - frame_h//20), cv2.FONT_HERSHEY_COMPLEX, 1, color=(0, 0, 255), thickness=2)

    images.append(frame)
    file_count += 1

    writefile = '/content/kadri/is42_{0:04d}.jpg'.format(file_count)
    cv2.imwrite(writefile, frame)
    # 20 в миллисекундах, попробуйте увеличить значение, скажем, 50 и
    # понаблюдайте за изменениями в показе
    
# Освободить объект захвата видео
vid_capture.release()
print('-----------------------------')
print('\nВремени на распознавание ушло: %.2f сек.' % (time.time() - start_time))

Фреймов в секунду:  29.97002997002997 FPS
Частота кадров:  372.0

-----------------------------
Для завершения нажмите "q" или Esc...
-----------------------------

Времени на распознавание ушло: 12.38 сек.


In [ ]:
def make_video(path, images, frame_w, frame_h, fps):
    '''
    Функция записывает видео из полученных массивов
    '''
    video_writer = cv2.VideoWriter(path,
                                cv2.VideoWriter_fourcc(*'MPEG'), 
                                fps, 
                                (frame_w, frame_h))

    # собираем все кадры в видео
    for i in range(len(images)):
        video_writer.write(images[i])

    # Ставим "точку", завершаем
    video_writer.release()

In [ ]:
# сборка видео по кадрам
path = '/content/video.mp4'
make_video(path, images, frame_w, frame_h, fps)

In [ ]:
# Запускаем
clip=VideoFileClip(path)
clip.ipython_display(width=800, center=False, fps=fps)

100%|██████████| 360/360 [00:01<00:00, 309.89it/s]


# mAP

In [ ]:
!rm -R downloads dataset 

# Загружаем репозиторий СОСО
!git clone https://github.com/nightrome/cocostuff.git
!cd cocostuff

# Загружаем валидационную выборку и файл аннотаций
!wget --directory-prefix=downloads http://images.cocodataset.org/zips/val2017.zip
!wget --directory-prefix=downloads http://images.cocodataset.org/annotations/annotations_trainval2017.zip

# Распаковываем
!mkdir -p dataset/images
!mkdir -p dataset/annotations
!unzip -q downloads/val2017.zip -d dataset/images/
!unzip -q downloads/annotations_trainval2017.zip -d dataset/annotations/

rm: cannot remove 'downloads': No such file or directory
rm: cannot remove 'dataset': No such file or directory
Cloning into 'cocostuff'...
remote: Enumerating objects: 335, done.
remote: Total 335 (delta 0), reused 0 (delta 0), pack-reused 335
Receiving objects: 100% (335/335), 3.47 MiB | 7.14 MiB/s, done.
Resolving deltas: 100% (172/172), done.
--2021-07-08 18:22:43--  http://images.cocodataset.org/zips/val2017.zip
Resolving images.cocodataset.org (images.cocodataset.org)... 52.217.133.233
Connecting to images.cocodataset.org (images.cocodataset.org)|52.217.133.233|:80... connected.
HTTP request sent, awaiting response... 200 OK
Length: 815585330 (778M) [application/zip]
Saving to: ‘downloads/val2017.zip’

val2017.zip         100%[===================>] 777.80M  48.7MB/s    in 16s     

2021-07-08 18:23:00 (47.3 MB/s) - ‘downloads/val2017.zip’ saved [815585330/815585330]

--2021-07-08 18:23:00--  http://images.cocodataset.org/annotations/annotations_trainval2017.zip
Resolving images.c

In [ ]:
# Делаем предсказание модели по всем проверочным фотографиям и записываем в файл
detection_res = []
counter = 0
for image_id in os.listdir('/content/dataset/images/val2017/'):
    counter += 1
    if counter % 10 == 0:
        clear_output()
        print(counter)
    path = f'/content/dataset/images/val2017/{image_id}'
    img = cv2.imread(path) # Загружаем фото
    results = model(img, size=640)# предикт 
    for i in range(len(results.pandas().xyxy[0])):
        res = results.pandas().xyxy[0].iloc[i] # Проходим по всем строчкам предсказания
        if len(zzz) != 0:
            detection_res.append({
                'score': float(res['confidence']),
                'category_id': int(res['class']) + 1,
                'bbox': [float(res['xmin']), 
                         float(res['ymin']), 
                         float(res['xmax']) - float(res['xmin']), 
                         float(res['ymax']) - float(res['ymin'])],
                'image_id': int(image_id.strip('0').replace('.jpg', ''))
            }) # Записываем нужные данные в словарь

with open('/content/detections.json', 'w') as jfile:
    json.dump(detection_res, jfile)

5000


In [ ]:
# Подсчет mAP с помощью cocotools
from pycocotools.coco import COCO
from pycocotools.cocoeval import COCOeval

anno_file = '/content/dataset/annotations/annotations/instances_val2017.json'
res_path = '/content/detections.json'

coco_gt = COCO(anno_file)
coco_dt = coco_gt.loadRes(res_path)

cocoEval = COCOeval(coco_gt, coco_dt, 'bbox')
cocoEval.params.catIds = [1] #person id : 1 - оставляем только людей
cocoEval.evaluate()
cocoEval.accumulate()
cocoEval.summarize()

loading annotations into memory...
Done (t=0.42s)
creating index...
index created!
Loading and preparing results...
DONE (t=0.05s)
creating index...
index created!
Running per image evaluation...
Evaluate annotation type *bbox*
DONE (t=4.15s).
Accumulating evaluation results...
DONE (t=0.36s).
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=   all | maxDets=100 ] = 0.534
 Average Precision  (AP) @[ IoU=0.50      | area=   all | maxDets=100 ] = 0.732
 Average Precision  (AP) @[ IoU=0.75      | area=   all | maxDets=100 ] = 0.582
 Average Precision  (AP) @[ IoU=0.50:0.95 | area= small | maxDets=100 ] = 0.321
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=medium | maxDets=100 ] = 0.617
 Average Precision  (AP) @[ IoU=0.50:0.95 | area= large | maxDets=100 ] = 0.752
 Average Recall     (AR) @[ IoU=0.50:0.95 | area=   all | maxDets=  1 ] = 0.198
 Average Recall     (AR) @[ IoU=0.50:0.95 | area=   all | maxDets= 10 ] = 0.550
 Average Recall     (AR) @[ IoU=0.50:0.95 | area=   all | maxDets